## Notebook to fetch and compile stonycreek into one excel file

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import xlsxwriter
import plotly.express as px
from datetime import datetime
import plotly.graph_objects as go
from datetime import datetime
from plotly.subplots import make_subplots
import requests
import io
import ipywidgets as widgets
from ipywidgets import HBox, VBox, interact
import numpy as np
from IPython.display import display
import re
from urllib.error import HTTPError
from pandas.errors import InvalidIndexError
from IPython.display import display, HTML, clear_output

pd.options.plotting.backend = "plotly"

In [2]:
SITE_PREFIX = "FCC"
SITE_NUMBERS = [f"0{x}" for x in (1, 2, 3, 4, 5, 6, 7, 8, 9, 11)] + ['10']
SITE_NAMES = [f"{SITE_PREFIX}{x}" for x in SITE_NUMBERS]
print(SITE_NAMES)
BASE_URL = "https://www.bosl.com.au/IoT/FCC/databases/"

['FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08', 'FCC09', 'FCC011', 'FCC10']


In [3]:
all_depth_vel_v1 = []
#all_depth_vel_v2 = []
#all_turb_temp_ec = []

def hit_website(url, **args):
    try:
        try:
            data = pd.read_csv(url, **args).dropna(how='all', axis='columns')
        except pd.errors.ParserError as e:
            print("Failed on:", url)
            raise e

        print(f"Hit: {url}")
        return data
    except HTTPError:
        print(f"Missed: {url}")
        return None

for site in SITE_NAMES:
    all_depth_vel_v1.append(hit_website(f"{BASE_URL}{site}.csv", names=[(x) for x in range(12)], skiprows=[0, 1]))
    #all_depth_vel_v2.append(hit_website(f"{BASE_URL}{site}_v2.csv"))
    #all_turb_temp_ec.append(hit_website(f"{BASE_URL}{site}_Dep_Turb.csv", 'warn', None, 1))

    # Misc data cleaning
    # 05-1 has extra row
    #if site == f"{SITE_PREFIX}05-1":
    #    all_data_v1[-1].drop(all_data_v1[-1].tail(1).index, inplace=True)

Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC01.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC02.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC03.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC04.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC05.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC06.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC07.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC08.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC09.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC011.csv
Hit: https://www.bosl.com.au/IoT/FCC/databases/FCC10.csv


In [4]:
for data_v1 in all_depth_vel_v1:
    if data_v1 is not None:
        data_v1.rename(columns={0:"DateTime", 7:"Peaks", 5:"Angle", 8:"Coarse_depth", 11:"Fine_depth_est"}, inplace=True)

In [5]:
site_id_1 = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
    value=SITE_NAMES[0]
)
def response(change):
    clear_output()
    display(site_id_1)
    idx = SITE_NAMES.index(site_id_1.value)
    display(all_depth_vel_v1[idx])
site_id_1.observe(response)
response(None)

Dropdown(description='Site:', options=('FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08',…

DateTime  1     4  Angle    6  \
0     30/11/22 04:27:18 AM  T  3307   2.69  297   
1     30/11/22 04:34:24 AM  T  3316   2.58  294   
2     06/12/22 06:03:28 AM  T  4061   3.33  292   
3     06/12/22 06:10:38 AM  T  4061   3.28  298   
4     06/12/22 06:17:42 AM  T  4060   4.07  286   
...                    ... ..   ...    ...  ...   
1481  13/12/22 04:44:20 AM  T  4019  73.88  247   
1482  13/12/22 04:51:22 AM  T  4018  73.67  268   
1483  13/12/22 04:51:25 AM  T  4018  73.67  268   
1484  13/12/22 04:58:28 AM  T  4012  73.86  273   
1485  13/12/22 05:05:41 AM  T  4013  73.85  277   

                                Peaks  Coarse_depth      9  10  Fine_depth_est  
0     1260B40|4360160|6600132|7C8011A           300  10.96   0             294  
1     1260C98|677013E|2540132|3D1011E           300  10.64   0             294  
2     1030A66|829013E|1E40136|65A0130           240  26.07   0             259  
3     1030A04|1D80138|6570132|3350126           240  32.05   0             259  
4     1014154|1D60388|2C20144|5680124           300  22.84   0             257  
...                               ...           ...    ...  ..             ...  
1481   FB0180|31F014A|599014A|1F10138          1440  10.57   0            1433  
1482  595021C|17B015E|250014E|3FE014C          1440  10.02   0            1429  
1483  595021C|17B015E|250014E|3FE014C          1440  10.02   0            1429  
1484   5B0038E|FF014E|2690134|3330120          1440  10.16   0            1456  
1485  5AA03D8|269014A|78B013E|3F00120          1440  11.09   0            1450  

[1486 rows x 10 columns]

In [6]:
all_merged_data = []
for idx, data_v1 in enumerate(all_depth_vel_v1):
    merged_data = data_v1
    merged_data.columns = merged_data.columns.astype(str)
    merged_data.dropna(how='all', subset=merged_data.columns, inplace=True)
    merged_data.dropna(axis=1, inplace=True, how='all')
    merged_data.dropna(subset=["Peaks"], inplace=True)
    try:
        def extract_peak(row):
            peaks = str(row["Peaks"]).split("|")
            try:
                decoded_peaks = [int(x[:3], 16) for x in peaks]
            except ValueError:
                decoded_peaks = [None] * len(peaks)
            finally:
                column_names = [f"DIST-{i+1}" for i in range(len(decoded_peaks))]
                return pd.Series(decoded_peaks, index=column_names)
        merged_data = pd.concat([merged_data, merged_data.apply(extract_peak, axis=1)], axis=1)
        depth_column_names = [col for col in merged_data.columns if 'DIST-' in col]
        
        merged_data["DateTime"] = pd.to_datetime(merged_data["DateTime"], format="%d/%m/%y %I:%M:%S %p")
        merged_data["DateTime"] =  merged_data["DateTime"].dt.tz_localize("UTC").dt.tz_convert("Australia/Broken_Hill")
        merged_data.dropna(subset=depth_column_names, axis='rows', inplace=True)

        all_merged_data.append(merged_data)
        merged_data.dropna(how='all', axis=1, inplace=True)
    except ValueError as e:
        print(merged_data)
        raise e
merged_data.dropna(how='all', axis=1, inplace=True)

In [7]:
KEEP_COLUMNS = ["DateTime", "SignalStrength", "Angle", "Peaks", "Velocity", "Course_depth", "Fine_depth_est"]
for merged_data in all_merged_data:
    columns_to_drop = [x for x in merged_data.columns if x not in KEEP_COLUMNS and "DIST-" not in x]
    merged_data.drop(columns_to_drop, axis=1, inplace=True)

In [8]:
site_id_3 = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
    value=SITE_NAMES[0]
)
def response(change):
    clear_output()
    display(site_id_3)
    idx = SITE_NAMES.index(site_id_3.value)
    display(all_merged_data[idx])
site_id_3.observe(response)
response(None)

Dropdown(description='Site:', options=('FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07', 'FCC08',…

DateTime  Angle                            Peaks  \
0    2022-11-30 14:57:18+10:30   2.69  1260B40|4360160|6600132|7C8011A   
1    2022-11-30 15:04:24+10:30   2.58  1260C98|677013E|2540132|3D1011E   
2    2022-12-06 16:33:28+10:30   3.33  1030A66|829013E|1E40136|65A0130   
3    2022-12-06 16:40:38+10:30   3.28  1030A04|1D80138|6570132|3350126   
4    2022-12-06 16:47:42+10:30   4.07  1014154|1D60388|2C20144|5680124   
...                        ...    ...                              ...   
1481 2022-12-13 15:14:20+10:30  73.88   FB0180|31F014A|599014A|1F10138   
1482 2022-12-13 15:21:22+10:30  73.67  595021C|17B015E|250014E|3FE014C   
1483 2022-12-13 15:21:25+10:30  73.67  595021C|17B015E|250014E|3FE014C   
1484 2022-12-13 15:28:28+10:30  73.86   5B0038E|FF014E|2690134|3330120   
1485 2022-12-13 15:35:41+10:30  73.85  5AA03D8|269014A|78B013E|3F00120   

      Fine_depth_est  DIST-1  DIST-2  DIST-3  DIST-4  
0                294     294    1078    1632    1992  
1                294     294    1655     596     977  
2                259     259    2089     484    1626  
3                259     259     472    1623     821  
4                257     257     470     706    1384  
...              ...     ...     ...     ...     ...  
1481            1433    4016     799    1433     497  
1482            1429    1429     379     592    1022  
1483            1429    1429     379     592    1022  
1484            1456    1456    4080     617     819  
1485            1450    1450     617    1931    1008  

[1486 rows x 8 columns]

Depth correction

In [9]:
CORRECTION_FACTORS = {'01':0, '02':0, '03':0, '04':0, '05':0, '06':0, '07':0, '08':0, '09':0, '10':0, '011':0}
for key, value in CORRECTION_FACTORS.items():
    idx = SITE_NUMBERS.index(key)
    # all_merged_data[idx]["DEPTH-True"] = value - all_merged_data[idx]["DIST-1"].multiply(np.sin(np.radians(all_merged_data[idx]["Angle"])), axis="index")
    all_merged_data[idx]["DEPTH-True"] = all_merged_data[idx]["DIST-1"].multiply(np.sin(np.radians(all_merged_data[idx]["Angle"])), axis="index")

Negative depths are removed

In [10]:
pd.DataFrame(zip(SITE_NAMES, (len(merged_data[merged_data["DEPTH-True"] < 0]) for merged_data in all_merged_data))).rename(columns={0:"Site", 1:"<0 Depths"})

Site  <0 Depths
0    FCC01         15
1    FCC02          2
2    FCC03        161
3    FCC04          8
4    FCC05          0
5    FCC06          2
6    FCC07          0
7    FCC08         10
8    FCC09          2
9   FCC011        408
10   FCC10        174

In [ ]:
site_id_2 = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
    value=SITE_NAMES[0]
)
def response(change):
    clear_output()
    display(site_id_2)
    idx = SITE_NAMES.index(site_id_2.value)
    display(all_merged_data[idx].loc[all_merged_data[idx]["DEPTH-True"] < 0])
site_id_2.observe(response)
response(None)

Dropdown(description='Site:', index=10, options=('FCC01', 'FCC02', 'FCC03', 'FCC04', 'FCC05', 'FCC06', 'FCC07'…

Empty DataFrame
Columns: [DateTime, Angle, Peaks, Fine_depth_est, DIST-1, DIST-2, DIST-3, DIST-4, DEPTH-True]
Index: []

In [12]:
for merged_data in all_merged_data:
    merged_data.drop(merged_data[merged_data["DEPTH-True"] < 0].index, inplace=True)

Velocity correction

In [13]:
# for merged_data in all_merged_data:
#     merged_data["Corrected Velocity"] = merged_data["Velocity"] / np.cos(np.radians(merged_data["Angle"]))
# display(merged_data)

In [28]:
fig = px.line(all_merged_data[0], x='DateTime', y=depth_column_names)
f2 = go.FigureWidget(fig)
site_id = widgets.Dropdown(
    options=SITE_NAMES,
    description='Site:',
    disabled=False,
)

def response(change):
    f2.update_layout(title=f"Depth data of {site_id.value}")
    site_idx = SITE_NAMES.index(site_id.value)
    with f2.batch_update():
        for idx, col in enumerate(depth_column_names):
            f2.data[idx].x = all_merged_data[site_idx]["DateTime"]
            f2.data[idx].y = all_merged_data[site_idx][col]
site_id.observe(response, names="value")
response(None)
widgets.VBox([site_id, f2])

In [29]:
earliest_date = min(list(x["DateTime"].min() for x in all_merged_data)).date()
latest_date = max(list(x["DateTime"].max() for x in all_merged_data)).date()
print(f"from {earliest_date} to {latest_date}")
url = f"https://api.melbournewater.com.au/rainfall-river-level/228378A/rain/hourly/range.csv?fromDate={earliest_date}&toDate={latest_date}"
print(url)
r = requests.get(url)
d = r.headers['content-disposition']
rain_filename = re.findall("filename=(.+)", d)[0]
rainfall_data = pd.read_csv(io.StringIO(r.content.decode('utf-8'))).dropna(how='all', axis='columns')

from 2022-09-13 to 2022-12-13
https://api.melbournewater.com.au/rainfall-river-level/228378A/rain/hourly/range.csv?fromDate=2022-09-11&toDate=2022-12-13


In [30]:
rainfall_data["Date/Time"] = pd.to_datetime(rainfall_data["Date/Time"], format="%Y/%m/%d %H:%M:%S").dt.tz_localize("Australia/Broken_Hill")
rainfall_data

Date/Time  Current rainfall (mm)  \
0    2022-12-13 15:00:00+10:30                    1.2   
1    2022-12-13 14:00:00+10:30                    0.6   
2    2022-12-13 13:00:00+10:30                    0.4   
3    2022-12-13 12:00:00+10:30                    0.0   
4    2022-12-13 11:00:00+10:30                    0.0   
...                        ...                    ...   
2240 2022-09-11 05:00:00+09:30                    0.0   
2241 2022-09-11 04:00:00+09:30                    0.0   
2242 2022-09-11 03:00:00+09:30                    0.0   
2243 2022-09-11 02:00:00+09:30                    0.0   
2244 2022-09-11 01:00:00+09:30                    0.0   

      Cumulative rainfall (mm)  
0                          2.2  
1                          1.0  
2                          0.4  
3                          0.0  
4                          0.0  
...                        ...  
2240                       0.0  
2241                       0.0  
2242                       0.0  
2243                       0.0  
2244                       0.0  

[2245 rows x 3 columns]

In [31]:
fig = rainfall_data.plot(x='Date/Time', y="Current rainfall (mm)", title=f"Rainfall of {rain_filename}").update_layout(
    xaxis_title="Time", yaxis_title=f"Rainfall (mm)"
)
fig.show()

Periods in which there is a >1 hr gap is ignored

In [32]:
time_filter = lambda x: x > 1 * 60 * 60

In [33]:
# fig = make_subplots(specs=[[{"secondary_y": True}]])
# fig.add_trace(go.Scatter(x=merged_data["DateTime"],
#     y=np.where(time_filter(merged_data['DateTime'].diff().dt.seconds), None, merged_data["DEPTH-True"]), 
#     name="Depth"),
#     secondary_y=False)
# fig.add_trace(go.Scatter(x=rainfall_data["Date/Time"], y=rainfall_data["Current rainfall (mm)"], name="Rainfall"), secondary_y=True)
# fig.update_yaxes(title_text="Depth (mm)", secondary_y=False)
# fig.update_yaxes(autorange="reversed", secondary_y=True)
# fig.update_yaxes(title_text="Rainfall (mm)", secondary_y=True)
# fig.update_xaxes(title_text="Time", tickangle=45, nticks=30)
# fig.update_layout(autosize=True, width=1100, height=700, legend=dict(title="Lines"), title=f"Rainfall vs Depth of {site}")
# fig.show()

In [34]:
fig = make_subplots(specs=[[{"secondary_y": True}]])
def display_col(source, col):
    for site_name, data in zip(SITE_NAMES, source):
        fig.add_trace(go.Scatter(mode = 'markers', x=data["DateTime"],
        y=np.where(time_filter(data['DateTime'].diff().dt.seconds), None, data[col]), 
        name=f"{col}:{site_name}"),
        secondary_y=False)

display_col(all_merged_data, "DEPTH-True")
display_col(all_merged_data, "Fine_depth_est")

fig.add_trace(go.Scatter(x=rainfall_data["Date/Time"], y=rainfall_data["Current rainfall (mm)"], name="Rainfall"), secondary_y=True)
# fig.update_yaxes(title_text="Depth (mm)", secondary_y=False, range = [0, 8000])
max_rainfall = rainfall_data["Current rainfall (mm)"].max()
fig.update_yaxes(range = [max_rainfall * 4, 0], secondary_y=True, title_text="Rainfall (mm)")
fig.update_xaxes(title_text="Time", tickangle=45, nticks=30)
fig.update_layout(autosize=False, width=1100, height=700, legend=dict(title="Lines"), title="All plots")

fig.show()

In [35]:
writer = pd.ExcelWriter(f'frankston-{datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")}.xlsx', engine='xlsxwriter')
def write_sheet(data, sheet_presfix = ""):
    for site_name, data in zip(SITE_NAMES, data):
        data["DateTime"] = data["DateTime"].dt.tz_localize(None)
        data.to_excel(writer, sheet_name=f"{sheet_presfix}{site_name}", index=False)
write_sheet(all_merged_data, "Radar-")
rainfall_data["Date/Time"] = rainfall_data["Date/Time"].dt.tz_localize(None)
rainfall_data.to_excel(writer, sheet_name=f"{rain_filename[:31]}", index=False)
writer.close()